## Импорт библиотек

In [1]:
import os
import numpy as np
import pandas as pd
from tqdm import tqdm
import matplotlib.pyplot as plt
import json

## Функции используемые для создания данных для обучения

In [2]:
def save_json_dataset(dset):
    number_samples = 1024
    for i in range(int(np.floor(len(dset) / number_samples))):
        with open(f'dp vetrical zones/vertical_center/dataset_{i}.json', 'w') as file:
            if i == np.floor(len(dset) / number_samples) - 1:
                json.dump(dset[i * number_samples:], file)
                print(f'dataset_{i} сохранен')
            else:
                json.dump(dset[i * number_samples:i * number_samples + number_samples], file)
                print(f'dataset_{i} сохранен')

def save_json_dataset_wall(dset):
    number_samples = 1024
    for i in range(int(np.floor(len(dset) / number_samples))):
        with open(f'dp vetrical zones/vertical_wall/dataset_{i}.json', 'w') as file:
            if i == np.floor(len(dset) / number_samples) - 1:
                json.dump(dset[i * number_samples:], file)
                print(f'dataset_{i} сохранен')
            else:
                json.dump(dset[i * number_samples:i * number_samples + number_samples], file)
                print(f'dataset_{i} сохранен')
             

def heigh_of_col(mrx, index):
    column = mrx[:, index]
    mask = column != -1
    count_non_negative = np.sum(mask)
    return count_non_negative

def max_width_spinneret(matrix_array):
    
    # Находим индексы элементов, не равных -1, для каждой строки 
    non_negative_indices = (matrix_array != -1)                          
                                                                            
    # Считаем количество элементов, не равных -1, для каждой строки      
    count_non_negative_elements = np.sum(non_negative_indices, axis=1)   
                                                                            
    # Находим индекс строки с максимальным количеством элементов, не равных -1
    max_row_index = np.argmax(count_non_negative_elements)
    max_width = count_non_negative_elements[max_row_index]
    
    return max_width

def width_row(matrix_array, row):
    # Находим индексы элементов, не равных -1, в выбранной строке
    non_negative_indices_in_selected_row = (matrix_array[row] != -1)

    # Считаем количество элементов, не равных -1, в выбранной строке
    count_non_negative_elements_in_selected_row = np.sum(non_negative_indices_in_selected_row)
    
    return count_non_negative_elements_in_selected_row

def length_to_elements(matrix_array, row, column):
    selected_row_part = matrix_array[row, :column + 1]
    non_negative_indices_in_selected_row_part = (selected_row_part != -1)
    count_non_negative_elements_in_selected_row_part = np.sum(non_negative_indices_in_selected_row_part)
    
    return count_non_negative_elements_in_selected_row_part

def process_matrix(mrx, dataset):
    
    max_width = max_width_spinneret(mrx) 

    for row in range(1, 201):
        for col in range(0, 203):
            if mrx[row, col] != -1:
                submrx = mrx[row - 1 : row + 1, col - 1: col + 2]
                if submrx[0, 0] != -1 and submrx[0, 2] !=-1:
                    wdh_pr = width_row(mrx, row - 1)
                    
                    wdh_r = width_row(mrx, row)
                    lng = length_to_elements(mrx, row, col)
                    hgt_c = heigh_of_col(mrx, col)

                    if row == 200:
                        wdh_next = width_row(mrx, row)
                    else:
                        wdh_next = width_row(mrx, row + 1)     
                    
                    central = submrx[1, 1]
                    outer = []
                    d4_d1 = wdh_pr / max_width
                    d2_d1 = wdh_r / max_width
                    d3_d2 = lng / wdh_r
                    d5_d1 = wdh_next / max_width
                    dyn_dy = (row + 1) / hgt_c
                    outer.append(row)
                    outer.append(col)
                    for x_offset, y_offset in [(0, 0), (0, 1), (0, 2)]:
                        outer_value = submrx[x_offset, y_offset]
                        outer.append(outer_value)

                    outer.append(d2_d1)
                    outer.append(d3_d2)
                    outer.append(d4_d1)
                    outer.append(dyn_dy)
                    outer.append(d5_d1)
                    outer.append(central)
                    dataset.append(outer)

def process_matrix_wall(mrx, dataset):
    
    max_width = max_width_spinneret(mrx) 

    for row in range(1, 201):
        for col in range(0, 203):
            if mrx[row, col] != -1:
                submrx = mrx[row - 1 : row + 1, col - 1: col + 2]
                if submrx[0, 0] == -1 or submrx[0, 2] == -1:
                    wdh_pr = width_row(mrx, row - 1)
                    
                    wdh_r = width_row(mrx, row)
                    lng = length_to_elements(mrx, row, col)
                    hgt_c = heigh_of_col(mrx, col)

                    if row == 200:
                        wdh_next = width_row(mrx, row)
                    else:
                        wdh_next = width_row(mrx, row + 1)     
                    
                    central = submrx[1, 1]
                    outer = []
                    d4_d1 = wdh_pr / max_width
                    d2_d1 = wdh_r / max_width
                    d3_d2 = lng / wdh_r
                    d5_d1 = wdh_next / max_width
                    dyn_dy = (row + 1) / hgt_c
                    outer.append(row)
                    outer.append(col)
                    for x_offset, y_offset in [(0, 0), (0, 1), (0, 2)]:
                        outer_value = submrx[x_offset, y_offset]
                        outer.append(outer_value)

                    outer.append(d2_d1)
                    outer.append(d3_d2)
                    outer.append(d4_d1)
                    outer.append(dyn_dy)
                    outer.append(d5_d1)
                    outer.append(central)
                    dataset.append(outer)
                
                          

   

## Получение названий файлов датасета

In [3]:
datasets = []

for filename in os.listdir('CSV dataset'):
    datasets.append(f'CSV dataset/{filename}')
print(datasets)    
   

['CSV dataset/Dataset_0.csv', 'CSV dataset/Dataset_1.csv', 'CSV dataset/Dataset_3.csv', 'CSV dataset/Dataset_4.csv']


In [ ]:
count = 0
for path in datasets:
    df = pd.read_csv(path)
    columns = list(df.columns)
    for column in columns[2:]:
        df.loc[(df['x'] == 1.01) & (df['y'] == 0), column] = -1
        df.loc[(df['x'] == -1.01) & (df['y'] == 0), column] = -1
    path_new = f'CSV dataset/Dataset{count}.csv'
    df.to_csv(path_new, index = False, na_rep = 'NaN')
    count += 1   

## Создание матриц для каждого файла из всех столбцов

In [4]:
def create_matrixes(columns, df, matrixes):
    for column in columns:
        matrix = pd.pivot_table(df, values=column, index='y', columns='x', fill_value=-1)
        mrx = np.flipud(matrix.to_numpy())
        matrixes.append(mrx)

In [7]:
step_x = 0.01
step_y = 0.01
columns = []
matrixes = []

df = pd.read_csv(datasets[0])
columns.append(list(df.columns[2:]))
print(columns)
print(len(columns))
indexs = [0, 1, 10, 11]
create_matrixes(columns[0][0:27], df, matrixes)

[['spf.U (m/s) @ v0=0.02_y2=3E-4', 'spf.U (m/s) @ v0=0.02_y2=3.5E-4', 'spf.U (m/s) @ v0=0.02_y2=4E-4', 'spf.U (m/s) @ v0=0.02_y2=4.5E-4', 'spf.U (m/s) @ v0=0.02_y2=5E-4', 'spf.U (m/s) @ v0=0.02_y2=5.5E-4', 'spf.U (m/s) @ v0=0.02_y2=6E-4', 'spf.U (m/s) @ v0=0.02_y2=6.5E-4', 'spf.U (m/s) @ v0=0.02_y2=7E-4', 'spf.U (m/s) @ v0=0.02_y2=7.5E-4', 'spf.U (m/s) @ v0=0.02_y2=8E-4', 'spf.U (m/s) @ v0=0.02_y2=8.5E-4', 'spf.U (m/s) @ v0=0.02_y2=9E-4', 'spf.U (m/s) @ v0=0.02_y2=9.5E-4', 'spf.U (m/s) @ v0=0.02_y2=0.001', 'spf.U (m/s) @ v0=0.02_y2=0.00105', 'spf.U (m/s) @ v0=0.02_y2=0.0011', 'spf.U (m/s) @ v0=0.02_y2=0.00115', 'spf.U (m/s) @ v0=0.02_y2=0.0012', 'spf.U (m/s) @ v0=0.02_y2=0.00125', 'spf.U (m/s) @ v0=0.02_y2=0.0013', 'spf.U (m/s) @ v0=0.02_y2=0.00135', 'spf.U (m/s) @ v0=0.02_y2=0.0014', 'spf.U (m/s) @ v0=0.02_y2=0.00145', 'spf.U (m/s) @ v0=0.02_y2=0.0015', 'spf.U (m/s) @ v0=0.04_y2=3E-4', 'spf.U (m/s) @ v0=0.04_y2=3.5E-4', 'spf.U (m/s) @ v0=0.04_y2=4E-4', 'spf.U (m/s) @ v0=0.04_y2=4.5E-4

In [6]:
i = 0
for column in columns[0]:
    print(i)
    print(column)
    i += 1

0
spf.U (m/s) @ v0=0.02_y2=3E-4
1
spf.U (m/s) @ v0=0.02_y2=3.5E-4
2
spf.U (m/s) @ v0=0.02_y2=4E-4
3
spf.U (m/s) @ v0=0.02_y2=4.5E-4
4
spf.U (m/s) @ v0=0.02_y2=5E-4
5
spf.U (m/s) @ v0=0.02_y2=5.5E-4
6
spf.U (m/s) @ v0=0.02_y2=6E-4
7
spf.U (m/s) @ v0=0.02_y2=6.5E-4
8
spf.U (m/s) @ v0=0.02_y2=7E-4
9
spf.U (m/s) @ v0=0.02_y2=7.5E-4
10
spf.U (m/s) @ v0=0.02_y2=8E-4
11
spf.U (m/s) @ v0=0.02_y2=8.5E-4
12
spf.U (m/s) @ v0=0.02_y2=9E-4
13
spf.U (m/s) @ v0=0.02_y2=9.5E-4
14
spf.U (m/s) @ v0=0.02_y2=0.001
15
spf.U (m/s) @ v0=0.02_y2=0.00105
16
spf.U (m/s) @ v0=0.02_y2=0.0011
17
spf.U (m/s) @ v0=0.02_y2=0.00115
18
spf.U (m/s) @ v0=0.02_y2=0.0012
19
spf.U (m/s) @ v0=0.02_y2=0.00125
20
spf.U (m/s) @ v0=0.02_y2=0.0013
21
spf.U (m/s) @ v0=0.02_y2=0.00135
22
spf.U (m/s) @ v0=0.02_y2=0.0014
23
spf.U (m/s) @ v0=0.02_y2=0.00145
24
spf.U (m/s) @ v0=0.02_y2=0.0015
25
spf.U (m/s) @ v0=0.04_y2=3E-4
26
spf.U (m/s) @ v0=0.04_y2=3.5E-4
27
spf.U (m/s) @ v0=0.04_y2=4E-4
28
spf.U (m/s) @ v0=0.04_y2=4.5E-4
29
spf.U 

In [16]:
matrixes

[array([[-1.00000000e+00,  0.00000000e+00,  5.87950710e-04, ...,
          5.87964604e-04,  0.00000000e+00, -1.00000000e+00],
        [-1.00000000e+00,  0.00000000e+00,  5.87659096e-04, ...,
          5.87682593e-04,  0.00000000e+00, -1.00000000e+00],
        [-1.00000000e+00,  0.00000000e+00,  5.87365769e-04, ...,
          5.87335908e-04,  0.00000000e+00, -1.00000000e+00],
        ...,
        [-1.00000000e+00, -1.00000000e+00, -1.00000000e+00, ...,
         -1.00000000e+00, -1.00000000e+00, -1.00000000e+00],
        [-1.00000000e+00, -1.00000000e+00, -1.00000000e+00, ...,
         -1.00000000e+00, -1.00000000e+00, -1.00000000e+00],
        [-1.00000000e+00, -1.00000000e+00, -1.00000000e+00, ...,
         -1.00000000e+00, -1.00000000e+00, -1.00000000e+00]]),
 array([[-1.00000000e+00,  0.00000000e+00,  5.87666717e-04, ...,
          5.87641893e-04,  0.00000000e+00, -1.00000000e+00],
        [-1.00000000e+00,  0.00000000e+00,  5.87376563e-04, ...,
          5.87337556e-04,  0.00000000e

In [8]:
len(matrixes)

27

In [11]:
dset_example = []
df = pd.DataFrame(columns=['row','col','v1','v2','v3', 'd2_d1', 'd3_d2', 'd4_d1', 'dyn_dy', 'd5_d1', 'central'])
process_matrix(matrixes[0], df)
print(df)
len(dset_example)

C:\Users\190782\AppData\Local\Temp\ipykernel_15824\3620846579.py:99: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  dataset.append(outer)
C:\Users\190782\AppData\Local\Temp\ipykernel_15824\3620846579.py:99: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  dataset.append(outer)
C:\Users\190782\AppData\Local\Temp\ipykernel_15824\3620846579.py:99: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  dataset.append(outer)
C:\Users\190782\AppData\Local\Temp\ipykernel_15824\3620846579.py:99: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  dataset.append(outer)
C:\Users\190782\AppData\Local\Temp\ipykernel_15824\3620846579.py:99: FutureWarning: The frame.ap

KeyboardInterrupt: 

In [10]:
dset = []
indexs = [0, 1, 25, 26]
for i in indexs:
    process_matrix(matrixes[i], dset)
df = pd.DataFrame(dset)
columns = ['row','col','v1','v2','v3', 'd2_d1', 'd3_d2', 'd4_d1', 'dyn_dy', 'd5_d1', 'central']
df.columns = columns
df.to_csv('DS6.csv', index=False)
df
    

row  col        v1        v2            v3     d2_d1     d3_d2  \
0         1    2  0.000000  0.000588  1.169852e-03  1.000000  0.009950   
1         1    3  0.000588  0.001170  1.746375e-03  1.000000  0.014925   
2         1    4  0.001170  0.001746  2.318073e-03  1.000000  0.019900   
3         1    5  0.001746  0.002318  2.882437e-03  1.000000  0.024876   
4         1    6  0.002318  0.002882  3.441727e-03  1.000000  0.029851   
...     ...  ...       ...       ...           ...       ...       ...   
135279  200  101  1.120742  1.161819  1.111384e+00  0.054726  0.545455   
135280  200  102  1.161819  1.111384  1.031102e+00  0.054726  0.636364   
135281  200  103  1.111384  1.031102  7.853527e-01  0.054726  0.727273   
135282  200  104  1.031102  0.785353  4.403242e-01  0.054726  0.818182   
135283  200  105  0.785353  0.440324  1.786996e-15  0.054726  0.909091   

           d4_d1    dyn_dy     d5_d1   central  
0       1.000000  0.011696  1.000000  0.000588  
1       1.000000  0.011696  1.000000  0.001169  
2       1.000000  0.011696  1.000000  0.001745  
3       1.000000  0.011696  1.000000  0.002317  
4       1.000000  0.011696  1.000000  0.002881  
...          ...       ...       ...       ...  
135279  0.054726  1.000000  0.054726  1.146251  
135280  0.054726  1.000000  0.054726  1.129945  
135281  0.054726  1.000000  0.054726  1.000205  
135282  0.054726  1.000000  0.054726  0.798442  
135283  0.054726  1.000000  0.054726  0.456509  

[135284 rows x 11 columns]

In [11]:
dset = []
# for mrx in matrixes:
#     process_matrix_wall(mrx, dset)
for i in indexs:
    process_matrix_wall(matrixes[i], dset)
df = pd.DataFrame(dset)
columns = ['row','col','v1','v2','v3', 'd2_d1', 'd3_d2', 'd4_d1', 'dyn_dy', 'd5_d1', 'central']
df.columns = columns
df.to_csv('DS6_wall.csv', index=False)
df

row  col        v1            v2        v3     d2_d1     d3_d2  \
0       1    1 -1.000000  0.000000e+00  0.000588  1.000000  0.004975   
1       1  201  0.000588  0.000000e+00 -1.000000  1.000000  1.000000   
2       2    1 -1.000000  0.000000e+00  0.000588  1.000000  0.004975   
3       2  201  0.000588  0.000000e+00 -1.000000  1.000000  1.000000   
4       3    1 -1.000000  0.000000e+00  0.000587  1.000000  0.004975   
...   ...  ...       ...           ...       ...       ...       ...   
1571  198  106  0.443931  1.849644e-15 -1.000000  0.054726  1.000000   
1572  199   96 -1.000000  2.165181e-15  0.437175  0.054726  0.090909   
1573  199  106  0.440014  2.005579e-15 -1.000000  0.054726  1.000000   
1574  200   96 -1.000000  2.344295e-15  0.437413  0.054726  0.090909   
1575  200  106  0.440324  1.786996e-15 -1.000000  0.054726  1.000000   

         d4_d1    dyn_dy     d5_d1       central  
0     1.000000  0.011696  1.000000  0.000000e+00  
1     1.000000  0.011696  1.000000  0.000000e+00  
2     1.000000  0.017544  1.000000  0.000000e+00  
3     1.000000  0.017544  1.000000  0.000000e+00  
4     1.000000  0.023392  1.000000  0.000000e+00  
...        ...       ...       ...           ...  
1571  0.054726  0.990050  0.054726  2.005579e-15  
1572  0.054726  0.995025  0.054726  2.344295e-15  
1573  0.054726  0.995025  0.054726  1.786996e-15  
1574  0.054726  1.000000  0.054726  2.696792e-15  
1575  0.054726  1.000000  0.054726  2.444047e-15  

[1576 rows x 11 columns]

In [20]:
print(len(dset))




1378


In [ ]:
type(matrixes[0])

In [ ]:
save_json_dataset(dset)
save_json_dataset_wall(dset_wall)

In [ ]:
prediction_values = []
input_values = []
for item in tqdm(dset):
    prediction_values.append(item['output'])
    input_values.append(item['input'])

    